In [1]:
import pandas as pd

import general_utils
%load_ext autoreload
%autoreload 2
%aimport algorithm_utils

In [2]:
from algorithm_utils import *
import general_utils as gu

In [3]:
timeframe = "15m"
higher_timeframe = general_utils.find_higher_timeframe(timeframe)

In [4]:
testing_length = 0
start_index = -8 * testing_length - 1
pair_name = "BTCUSDT"

original_pair_df: pd.DataFrame = gu.load_local_data(pair_name=pair_name, timeframe=timeframe)

if testing_length > 0:
    pair_df: pd.DataFrame = original_pair_df.iloc[start_index:start_index + testing_length].reset_index(drop=True)
else:
    pair_df: pd.DataFrame = original_pair_df

# Higher timeframe data for determining starting point
htf_pair_df: pd.DataFrame = gu.load_higher_tf_data(pair_name=pair_name, timeframe=higher_timeframe)

print("LTF length is", len(pair_df))
print("HTF length is", len(htf_pair_df))

LTF length is 70177
HTF length is 4939


In [5]:
gu.reset_logs()

print("Original pair_df starting point is at time", pair_df.iloc[0].time)

algo = Algo(pair_df, pair_name, allowed_verbosity=3)
initial_data_start_time = algo.pair_df.iloc[0].time

corrected_pair_df = create_filtered_pair_df_with_corrected_starting_point(htf_pair_df, initial_data_start_time,
                                                                          original_pair_df, timeframe, higher_timeframe)

print("Updated pair_df starting point to", corrected_pair_df.iloc[0].time)

algo = Algo(corrected_pair_df, "BTCUSDT", allowed_verbosity=1)

algo.init_zigzag(last_pivot_type="valley", last_pivot_candle_pdi=0)
h_o_starting_point: int = algo.zigzag_df.iloc[0].pdi

algo.calc_h_o_zigzag(h_o_starting_point)

# corrected_pair_df = pair_df.copy()

# print("Updated pair_df starting point to", corrected_pair_df.iloc[0].time)

# algo = Algo(corrected_pair_df, pair_name, allowed_verbosity=3)

# algo.init_zigzag(last_pivot_type="peak", last_pivot_candle_pdi=3)

# h_o_starting_point: int = algo.zigzag_df.iloc[0].pdi

# algo.calc_h_o_zigzag(h_o_starting_point)


# algo.h_o_indices.append(87)
# algo.h_o_indices.append(315)
# algo.h_o_indices.append(431)
# print(algo.find_lpls())
# h_o_zigzag_df = generate_h_o_zigzag(zigzag_df)
# pbos_df = h_o_zigzag_df.loc[h_o_zigzag_df.is_pbos]
# bos_df = find_confirmed_boss(pbos_df, pair_df)
# lpl_df = find_lpls(bos_df, zigzag_df)
# lplb_df = find_lplbs(bos_df, zigzag_df)

# boxes_list = []
# for lpl in lpl_df.itertuples():
#     start_index = lpl.pair_df_index
#     base_candle = Candle.create(pair_df.iloc[lpl.pair_df_index])
#     box_type = "long" if lpl.pivot_type == "valley" else "short"
#     box_to_add = Box(base_candle, b|ox_type)
#     box_to_add.check_box_ent

#     ries(pair_df)
#     boxes_list.append(box_to_add)


Original pair_df starting point is at time 2022-10-12 00:00:00
2022-11-05 00:00:00
Updated pair_df starting point to 2022-11-05 03:15:00
('Added starting point', Timestamp('2022-11-05 04:45:00'))
('',)
('Added BOS', Timestamp('2022-11-05 06:15:00'))
('CHOCH #', Timestamp('2022-11-05 04:45:00'), 'break at', Timestamp('2022-11-05 08:00:00'))
('Setting pattern start to', Timestamp('2022-11-05 06:15:00'))
('',)
('Added BOS', Timestamp('2022-11-05 14:45:00'))
('BOS #', Timestamp('2022-11-05 14:45:00'), 'break at', Timestamp('2022-11-06 01:45:00'))
('Added extremum of type', 'highest high', 'at', Timestamp('2022-11-05 20:30:00'))
('Setting pattern start to', Timestamp('2022-11-06 01:30:00'))
('',)
('Added BOS', Timestamp('2022-11-08 15:15:00'))
('BOS #', Timestamp('2022-11-08 15:15:00'), 'break at', Timestamp('2022-11-08 18:00:00'))
('Added extremum of type', 'highest high', 'at', Timestamp('2022-11-08 16:30:00'))
('Setting pattern start to', Timestamp('2022-11-08 16:30:00'))
('',)
('Added B

In [6]:
for segment in algo.segments:
    print(segment)
    segment.filter_candlestick_range(algo)
    segment.find_order_blocks(algo)
    for ob in segment.ob_list:
        position_entry_pdi = ob.position.find_entry_within_segment(segment)
        if position_entry_pdi is not None:
            ob.position.enter(position_entry_pdi)

    for ob in segment.ob_list:
        if ob.position.status != "ENTERED":
            continue

        exit_check_candles: pd.DataFrame = algo.pair_df.iloc[ob.position.entry_pdi:]
        candle_sentiments: pd.Series = exit_check_candles.apply(lambda candle: ob.position.detect_candle_sentiment(candle), axis=1)

        # Find the first instance where a STOPLOSS or FULL_TARGET happens in the candle_sentiments Series.
        mask = candle_sentiments.apply(lambda row: row[0] == "FULL_TARGET" or row[0] == "STOPLOSS")
        exit_index = mask.idxmax() if mask.any() else None

        if exit_index is not None:
            exit_code = candle_sentiments.loc[exit_index][0]
            # If the first exit event to happen is a full target, that means we have the maximum profit, and we exit the position.
            if exit_code == "FULL_TARGET":
                # This snippet is used to register each target individually, before the full target event happens. This is used for validating target
                # hits and troubleshoot bugs later using the ob.position.target_hit_pdis property which stores the PDI's of the candles that hit 
                # the targets.
                targets_before_full_target_cum_max: pd.Series = candle_sentiments.loc[:exit_index].apply(
                    lambda row: row[1] if row[0] == "TARGET" else 0).cummax()
                max_target_changes: pd.Series = targets_before_full_target_cum_max[targets_before_full_target_cum_max.diff() > 0]

                # Register the targets before the final full target
                for target_id, target_hit_pdi in zip(max_target_changes.values, max_target_changes.index):
                    ob.position.register_target(target_id, target_hit_pdi)

                # Register the final, full target
                ob.position.register_target(len(ob.position.target_list), exit_index)

                # Exit the position
                ob.position.exit(exit_code="FULL_TARGET", exit_pdi=exit_index)


            # If the first exit event to happen is a stoploss, we must check what the highest target reached was.
            elif exit_code == "STOPLOSS":
                # This snippet is used to register each target individually, before the stoploss event happens.
                targets_before_stoploss_cum_max: pd.Series = candle_sentiments.loc[:exit_index].apply(
                    lambda row: row[1] if row[0] == "TARGET" else 0).cummax()
                max_target_changes: pd.Series = targets_before_stoploss_cum_max[targets_before_stoploss_cum_max.diff() > 0]

                # Register the targets before the final full target
                for target_id, target_hit_pdi in zip(max_target_changes.values, max_target_changes.index):
                    ob.position.register_target(target_id, target_hit_pdi)

                ob.position.exit(exit_code="STOPLOSS", exit_pdi=exit_index)

        # print(ob) 
        # print("TARGETS", ob.position.target_list)
        # print("STOPLOSS", ob.position.stoploss)
        # print("FIRST EXIT INDEX", exit_index)   
        # print(candle_sentiments.iloc[exit_index])

Ascending segment starting at 6 ending at 19 OB formation at 23
Descending segment starting at 12 ending at 89 OB formation at 50
Descending segment starting at 69 ending at 346 OB formation at 342
Descending segment starting at 341 ending at 6709 OB formation at 528
Ascending segment starting at 459 ending at 7362 OB formation at 7054
Ascending segment starting at 7157 ending at 7849 OB formation at 7473
Ascending segment starting at 7558 ending at 8224 OB formation at 7962
Ascending segment starting at 7961 ending at 8532 OB formation at 8284
Ascending segment starting at 8333 ending at 9280 OB formation at 8557
Descending segment starting at 8534 ending at 9361 OB formation at 9361
Descending segment starting at 9360 ending at 9557 OB formation at 9490
Ascending segment starting at 9385 ending at 9741 OB formation at 9580
Ascending segment starting at 9658 ending at 11964 OB formation at 9972
Descending segment starting at 9938 ending at 12421 OB formation at 12043
Ascending segment

In [8]:
pt = gu.PlottingTool(width=1400, height=800)
pt.draw_candlesticks(corrected_pair_df)
pt.draw_zigzag(algo.zigzag_df)

pt.draw_points_with_label(algo.zigzag_df[algo.zigzag_df.pdi.isin(algo.h_o_indices)].pdi,
                          algo.zigzag_df[algo.zigzag_df.pdi.isin(algo.h_o_indices)].pivot_value,
                          draw_line=True)

for segment in algo.segments:
    # for ob in segment.ob_list:
    if segment.formation_method == "bos":
        pt.draw_segment_bbox(segment)
    else:
        pt.draw_segment_bbox(segment, color="red")
        # pt.draw_box(ob, algo.pair_df.iloc[-1].name)
# 
pt.show()

In [9]:
import pandas as pd
from openpyxl import load_workbook


def generate_positions_excel(output_file):
    # List to store position data
    positions_data = []

    # Iterate through each segment in the Algo object
    for segment in algo.segments:
        # Iterate through each order block in the segment
        for ob in segment.ob_list:
            # Extract the position information
            position = ob.position
            if len(position.target_hit_pdis) == 1:
                target_hit_times_list = [algo.convert_pdis_to_times(position.target_hit_pdis)]

            else:
                target_hit_times_list = algo.convert_pdis_to_times(position.target_hit_pdis)

            position_data = {
                'Position ID': position.parent_ob.id,
                'Status': position.status,
                'Net profit': position.net_profit,
                # 'Has been replaced?': position.parent_ob.has_been_replaced,
                'Ranking within segment': position.parent_ob.ranking_within_segment,
                'Quantity': position.qty,
                'Entry time': algo.convert_pdis_to_times(position.entry_pdi),
                'Exit time': algo.convert_pdis_to_times(position.exit_pdi),
                'Target hit times': [time.strftime("%Y-%m-%d %X") for time in target_hit_times_list],
                'Type': position.type,
                'Entry price': position.entry_price,
                'Stoploss': position.stoploss,
                'Target list': [round(float(target), 6) for target in position.target_list]
            }
            # Append the position data to the list
            positions_data.append(position_data)

    # Convert the list of dictionaries to a pandas DataFrame
    df = pd.DataFrame(positions_data)

    # Write the DataFrame to an Excel file
    df.to_excel(output_file, index=False)

    # Adjust column widths
    adjust_column_widths(output_file)


def adjust_column_widths(output_file):
    # Load the workbook and select the active worksheet
    wb = load_workbook(output_file)
    ws = wb.active

    # Adjust column widths
    for col in ws.columns:
        max_length = 0
        column = col[0].column_letter  # Get the column name
        for cell in col:
            try:
                if len(str(cell.value)) > max_length:
                    max_length = len(cell.value)
            except:
                pass
        adjusted_width = (max_length + 2)
        ws.column_dimensions[column].width = adjusted_width

    # Save the workbook
    wb.save(output_file)


# Example usage
# Assuming algo is an instance of the Algo class
generate_positions_excel(f'positions-{pair_name}.xlsx')

In [10]:
positions_data_df = pd.read_excel(f'positions-{pair_name}.xlsx')

total_positions_found = len(positions_data_df)
entered_positions = len(positions_data_df[positions_data_df["Status"] != "ACTIVE"])

positive_positions = len(positions_data_df[positions_data_df["Net profit"] > 0])
negative_positions = len(positions_data_df[positions_data_df["Net profit"] < 0])
winrate = positive_positions / entered_positions

full_target_positions = len(positions_data_df[positions_data_df["Status"].str.startswith("FULL_TARGET")])
no_target_positions = len(positions_data_df[positions_data_df["Status"].str.startswith("STOPLOSS")])
target_1_positions = len(positions_data_df[positions_data_df["Status"].str.startswith("TARGET_1")])
target_2_positions = len(positions_data_df[positions_data_df["Status"].str.startswith("TARGET_2")])

long_positions = len(positions_data_df[positions_data_df["Type"] == "short"])
short_positions = len(positions_data_df[positions_data_df["Type"] == "short"])

total_profit = positions_data_df["Net profit"].sum()
total_negative = positions_data_df[positions_data_df["Net profit"] < 0]["Net profit"].sum()
total_positive = positions_data_df[positions_data_df["Net profit"] > 0]["Net profit"].sum()

# Print the report
print(pair_name, "\n")
print("Over 2 years (Oct 12th 2022 - Oct 12th 2024)\n")
print(f"{total_positions_found} total positions found")
print(f"{entered_positions} total positions entered - no positions without exit\n")
print(f"{positive_positions} positive PnL")
print(f"{negative_positions} negative PnL")
print(f"({winrate:.0%} winrate)\n")
print(f"{full_target_positions} full targets achieved")
print(f"{no_target_positions} no target hit")
print(f"{target_1_positions} target_1 achieved")
print(f"{target_2_positions} target_2 achieved\n")
print(f"{long_positions} long positions")
print(f"{short_positions} short positions\n")
print(f"{total_profit:.2f} total profit")
print(f"{total_negative:.2f} total negative")
print(f"{total_positive:.2f} total positive")

BTCUSDT 

Over 2 years (Oct 12th 2022 - Oct 12th 2024)

448 total positions found
153 total positions entered - no positions without exit

60 positive PnL
93 negative PnL
(39% winrate)

52 full targets achieved
89 no target hit
4 target_1 achieved
8 target_2 achieved

181 long positions
181 short positions

31.72 total profit
-1110.09 total negative
1141.81 total positive


In [10]:
# Generate the times for the zigzag_df pivots

lo_zigzag_times: pd.Series = algo.convert_pdis_to_times(algo.zigzag_df.pdi)
lo_zigzag_times.to_csv(f"zigzag_times-{pair_name}.csv")

In [11]:
for segment in algo.segments:
    for ob in segment.ob_list:
        if ob.position.status.startswith("FULL_TARGET"):
            entry_to_stoploss = abs(ob.position.entry_price - ob.position.stoploss)

            if ob.position.type == "long":
                stoploss_pdi = algo.pair_df[algo.pair_df.low <= ob.position.stoploss].iloc[ob.position.entry_pdi:].first_valid_index()

                if stoploss_pdi is not None:
                    max_target_level = algo.pair_df.iloc[ob.position.entry_pdi:stoploss_pdi].high.max()
                    max_rr = abs(max_target_level - ob.position.entry_price) / entry_to_stoploss
                    print(ob.position.type, max_rr)

            else:
                stoploss_pdi = algo.pair_df[algo.pair_df.high >= ob.position.stoploss].iloc[ob.position.entry_pdi:].first_valid_index()

                if stoploss_pdi is not None:
                    max_target_level = algo.pair_df.iloc[ob.position.entry_pdi:stoploss_pdi].low.min()
                    max_rr = abs(max_target_level - ob.position.entry_price) / entry_to_stoploss
                    print(ob.position.type, max_rr)

short 39.38533333333333
long 6.07631412286252
long 7.307501378929825
short 4.103309481216485
long 9.119626168224299
long 21.000541711809486
long 35.078849721705915
short 41.64943820224718
short 26.310264385692367
long 5.3348082595873745
short 21.639250191277615
short 78.84285714285714
short 13.985161290322585
short 14.829704510108183
short 9.27971646673967
long 10.510025062656688
long 20.15523576240012
long 11.868184733804163
long 4.750149253731352
long 11.465063861758201
long 6.746197252207951
long 3.773391812865534
long 11.755162241888241
long 23.677083333333332
long 4.111797752808956
